In [5]:
import os
import glob

import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn

import scipy
from scipy import signal
from scipy.signal import freqz

import math

from butterworth import band_pass, low_pass, high_pass, band_stop
from utils import full_wave_rectify, plot_signal_one, plot_multiple, getEMGfeatures, toDataframe

In [6]:
# Setup the parameters of signal
f = 2000

In [7]:
pathEmg = r'/home/jerry/GitHub/EMG_regressive_model/data_process/raw_data/type2/emg'

emg_files = glob.glob(pathEmg+'/*.csv')
dfList = []

for filename in emg_files:
    headers = [*pd.read_csv(filename, nrows  = 1)]
    df = pd.read_csv(filename, usecols=[c for c in headers if c != 'time'])
    dfList.append(df)

#Concatenate individual column dataframes into one data frame (don't forget axis)
emgData = pd.concat(dfList, axis = 1)

pathElbow = r'/home/jerry/GitHub/EMG_regressive_model/data_process/raw_data/type2/kin'
imu_files = glob.glob(pathEmg+'/*.csv')

dfList2 = []

for filename in imu_files:
    headers = [*pd.read_csv(filename, nrows  = 1)]
    df = pd.read_csv(filename, usecols=[c for c in headers if c != 'time'])
    dfList2.append(df)
#Concatenate individual column dataframes into one data frame (don't forget axis)
angleData = pd.concat(dfList2, axis = 1)
angle = angleData.to_numpy()

In [12]:
#Convert the dataframe to numpy array
emg = emgData.to_numpy()
time = np.array([i/f for i in range(0, len(emg), 1)]) # sampling rate 2000 Hz
mean = np.mean(emg, axis = 0)
emgAvg = emg - mean
rawRect = full_wave_rectify(emgAvg)

In [24]:
#Filter the EMG data
emgSize = emgAvg.shape

bpEmg = np.zeros(emgSize)

for i in range(emgSize[-1]):
    input = emgAvg[:, i]
    iuput = input.T
    notch = band_stop(input, fs = f, fh = 2, fl = 20, order = 2)
    bandpass = low_pass(notch ,fs = f, low_pass = 20, order = 4)
    bpEmg[:, i] = bandpass

In [25]:
# erform the full wave rectification
rectEmg = full_wave_rectify(bpEmg)
print(rectEmg.shape)

(53480, 3)


In [26]:
tit = ['EMG CH1', 'EMG CH2', 'EMG CH3']
filename = 'emg_raw_lp_f4o10.png'
signal = [rawRect[:, 0], rawRect[:, 1], rawRect[:, 2]]
t = [time, time, time]

plot_multiple(signal, t, 3, 'Time', 'EMG', tit, filename)

In [27]:
tit = ['EMG CH1', 'EMG CH2', 'EMG CH3']
filename = 'emg_filter_lp_f200o10.png'
signal = [rectEmg[:, 0], rectEmg[:, 1], rectEmg[:, 2]]
t = [time, time, time]

plot_multiple(signal, t, 3, 'Time', 'EMG', tit, filename)